In [1]:
import pandas as pd
import numpy as np
import pickle
import re
import pyarrow.parquet as pq
from pyspark.sql import SparkSession

spark = SparkSession \
    .builder \
    .appName('Python Spark SQL basic example') \
    .config('spark.some.config.option', 'some-value') \
    .getOrCreate()

pd.set_option('display.max_columns', 40)
pd.set_option('display.max_rows', 5000)


In [ ]:
#df_2002 = spark.read.parquet('census_02.parquet')
#df_2007 = spark.read.load('census_07.parquet')
#df_2012 = spark.read.load('census_12.parquet')

In [17]:
def read_and_clean_USDA_census_parquet(input_parquet):
    """
    takes a parquet of one years USDA census of Agriculture data
    selects crops (ignores animals, economics/sales, etc)
    removes redundant, semi-redundant and just plain confusing data
    for more info see the README file at https://github.com/Rafael-SV/ag_census_analysis
    """
    dataframe_new = spark.read.parquet(input_parquet)
    dataframe_new.createOrReplaceTempView('dataframe_new')
    columns_to_select = 'DOMAIN_DESC,SECTOR_DESC,CLASS_DESC,PRODN_PRACTICE_DESC,COMMODITY_DESC,SHORT_DESC,UNIT_DESC,VALUE,YEAR,\
    COUNTY_NAME,COUNTY_CODE,ASD_DESC,STATE_ALPHA,STATISTICCAT_DESC'
    filtered_statisticcat_dataframe = spark.sql("SELECT {} FROM dataframe_new WHERE SECTOR_DESC = 'CROPS' \
        and (COMMODITY_DESC = 'COTTON' and CLASS_DESC='ALL CLASSES') \
        OR ( COMMODITY_DESC != 'COTTON' AND STATISTICCAT_DESC = 'AREA HARVESTED' OR 'STATISTICCAT_DESC' = 'AREA NOT HARVESTED' \
        OR STATISTICCAT_DESC = 'AREA IN PRODUCTION' OR STATISTICCAT_DESC = 'AREA BEARING' \
        OR STATISTICCAT_DESC = 'AREA NON-BEARING' OR STATISTICCAT_DESC = 'AREA GROWN')".format(columns_to_select))
    filtered_statisticcat_dataframe.createOrReplaceTempView("filtered_statisticcat_dataframe")
    #remove the aggregate totals except for the aggregate of the messy hay+haylage categories
    filtered_commodity_dataframe = spark.sql("SELECT {} FROM filtered_statisticcat_dataframe \
        WHERE COMMODITY_DESC NOT LIKE 'HAY' AND COMMODITY_DESC NOT LIKE 'HAYLAGE' AND COMMODITY_DESC NOT LIKE '%TOTALS' \
        AND COMMODITY_DESC NOT LIKE 'GRAIN STORAGE CAPAITY'".format(columns_to_select))
    filtered_commodity_dataframe.createOrReplaceTempView("filtered_commodity_dataframe")
    #remove categories based on irrigation pracitices
    filtered_unit_and_production_dataframe = spark.sql("\
        SELECT * FROM filtered_commodity_dataframe WHERE (UNIT_DESC LIKE 'OPERATIONS' OR UNIT_DESC LIKE 'SQ FT' \
        OR UNIT_DESC LIKE 'ACRES') AND PRODN_PRACTICE_DESC = 'ALL PRODUCTION PRACTICES' AND DOMAIN_DESC = 'TOTAL'")
    filtered_unit_and_production_dataframe.createOrReplaceTempView("filtered_unit_and_production_dataframe")
    return filtered_unit_and_production_dataframe
    

In [19]:
test_df = read_and_clean_USDA_census_parquet('census_02.parquet')
test_df.limit(100).toPandas().head(100)

DOMAIN_DESC SECTOR_DESC                 CLASS_DESC  \
0        TOTAL       CROPS                       SNAP   
1        TOTAL       CROPS                ALL CLASSES   
2        TOTAL       CROPS                ALL CLASSES   
3        TOTAL       CROPS                ALL CLASSES   
4        TOTAL       CROPS                ALL CLASSES   
5        TOTAL       CROPS                ALL CLASSES   
6        TOTAL       CROPS               NON-OIL TYPE   
7        TOTAL       CROPS                   OIL TYPE   
8        TOTAL       CROPS                ALL CLASSES   
9        TOTAL       CROPS                     WINTER   
10       TOTAL       CROPS                ALL CLASSES   
11       TOTAL       CROPS                ALL CLASSES   
12       TOTAL       CROPS                ALL CLASSES   
13       TOTAL       CROPS                ALL CLASSES   
14       TOTAL       CROPS                ALL CLASSES   
15       TOTAL       CROPS                ALL CLASSES   
16       TOTAL       CROPS                ALL CLASSES   
17       TOTAL       CROPS                ALL CLASSES   
18       TOTAL       CROPS                ALL CLASSES   
19       TOTAL       CROPS                ALL CLASSES   
20       TOTAL       CROPS               NON-OIL TYPE   
21       TOTAL       CROPS                   OIL TYPE   
22       TOTAL       CROPS                ALL CLASSES   
23       TOTAL       CROPS                     WINTER   
24       TOTAL       CROPS                ALL CLASSES   
25       TOTAL       CROPS                ALL CLASSES   
26       TOTAL       CROPS                ALL CLASSES   
27       TOTAL       CROPS                ALL CLASSES   
28       TOTAL       CROPS                ALL CLASSES   
29       TOTAL       CROPS                ALL CLASSES   
30       TOTAL       CROPS                ALL CLASSES   
31       TOTAL       CROPS                ALL CLASSES   
32       TOTAL       CROPS                ALL CLASSES   
33       TOTAL       CROPS                ALL CLASSES   
34       TOTAL       CROPS                ALL CLASSES   
35       TOTAL       CROPS                ALL CLASSES   
36       TOTAL       CROPS                ALL CLASSES   
37       TOTAL       CROPS                ALL CLASSES   
38       TOTAL       CROPS                ALL CLASSES   
39       TOTAL       CROPS                ALL CLASSES   
40       TOTAL       CROPS                ALL CLASSES   
41       TOTAL       CROPS                ALL CLASSES   
42       TOTAL       CROPS                ALL CLASSES   
43       TOTAL       CROPS                ALL CLASSES   
44       TOTAL       CROPS                ALL CLASSES   
45       TOTAL       CROPS                ALL CLASSES   
46       TOTAL       CROPS                ALL CLASSES   
47       TOTAL       CROPS                ALL CLASSES   
48       TOTAL       CROPS                ALL CLASSES   
49       TOTAL       CROPS                ALL CLASSES   
50       TOTAL       CROPS                ALL CLASSES   
51       TOTAL       CROPS                ALL CLASSES   
52       TOTAL       CROPS                ALL CLASSES   
53       TOTAL       CROPS                       SNAP   
54       TOTAL       CROPS                ALL CLASSES   
55       TOTAL       CROPS                ALL CLASSES   
56       TOTAL       CROPS                ALL CLASSES   
57       TOTAL       CROPS                ALL CLASSES   
58       TOTAL       CROPS                ALL CLASSES   
59       TOTAL       CROPS                ALL CLASSES   
60       TOTAL       CROPS                  CANTALOUP   
61       TOTAL       CROPS                  CANTALOUP   
62       TOTAL       CROPS                 WATERMELON   
63       TOTAL       CROPS                 WATERMELON   
64       TOTAL       CROPS                ALL CLASSES   
65       TOTAL       CROPS  GREEN, SOUTHERN (COWPEAS)   
66       TOTAL       CROPS  GREEN, SOUTHERN (COWPEAS)   
67       TOTAL       CROPS                ALL CLASSES   
68       TOTAL       CROPS                ALL CLASSES   
69       TOTA

In [18]:
## test cell to check spark sql queries
columns_to_select = 'DOMAIN_DESC,SECTOR_DESC,CLASS_DESC,PRODN_PRACTICE_DESC,COMMODITY_DESC,SHORT_DESC,UNIT_DESC,VALUE,YEAR,\
    COUNTY_NAME,COUNTY_CODE,ASD_DESC,STATE_ALPHA,STATISTICCAT_DESC'
dataframe_new = spark.read.parquet('census_02.parquet')
dataframe_new.createOrReplaceTempView('dataframe_new')
filtered_dataframe = spark.sql("SELECT {} FROM dataframe_new WHERE SECTOR_DESC = 'CROPS' \
    and (COMMODITY_DESC = 'COTTON' and CLASS_DESC='ALL CLASSES') \
    OR ( COMMODITY_DESC != 'COTTON' AND STATISTICCAT_DESC = 'AREA HARVESTED' OR 'STATISTICCAT_DESC' = 'AREA NOT HARVESTED' \
    OR STATISTICCAT_DESC = 'AREA IN PRODUCTION' OR STATISTICCAT_DESC = 'AREA BEARING' \
    OR STATISTICCAT_DESC = 'AREA NON-BEARING' OR STATISTICCAT_DESC = 'AREA GROWN')".format(columns_to_select))
filtered_dataframe.createOrReplaceTempView("filtered_statisticcat_dataframe")
filtered_dataframe.limit(100).toPandas().head(100)

DOMAIN_DESC SECTOR_DESC                          CLASS_DESC  \
0            TOTAL       CROPS                                SNAP   
1            TOTAL       CROPS                         ALL CLASSES   
2            TOTAL       CROPS                         ALL CLASSES   
3            TOTAL       CROPS                         ALL CLASSES   
4            TOTAL       CROPS                         ALL CLASSES   
5            TOTAL       CROPS                             ALFALFA   
6            TOTAL       CROPS                             ALFALFA   
7            TOTAL       CROPS                         SMALL GRAIN   
8            TOTAL       CROPS                                WILD   
9            TOTAL       CROPS                         ALL CLASSES   
10           TOTAL       CROPS                         ALL CLASSES   
11           TOTAL       CROPS                         ALL CLASSES   
12           TOTAL       CROPS                        NON-OIL TYPE   
13           TOTAL       CROPS                            OIL TYPE   
14           TOTAL       CROPS                         ALL CLASSES   
15           TOTAL       CROPS                              WINTER   
16           TOTAL       CROPS                         ALL CLASSES   
17           TOTAL       CROPS                         ALL CLASSES   
18           TOTAL       CROPS                         ALL CLASSES   
19           TOTAL       CROPS                      (EXCL ALFALFA)   
20           TOTAL       CROPS                         ALL CLASSES   
21           TOTAL       CROPS                         ALL CLASSES   
22  AREA HARVESTED       CROPS                         ALL CLASSES   
23  AREA HARVESTED       CROPS                         ALL CLASSES   
24  AREA HARVESTED       CROPS                         ALL CLASSES   
25  AREA HARVESTED       CROPS                         ALL CLASSES   
26  AREA HARVESTED       CROPS                         ALL CLASSES   
27  AREA HARVESTED       CROPS                         ALL CLASSES   
28  AREA HARVESTED       CROPS                         ALL CLASSES   
29           TOTAL       CROPS                         ALL CLASSES   
30           TOTAL       CROPS                         ALL CLASSES   
31           TOTAL       CROPS                         ALL CLASSES   
32           TOTAL       CROPS                         ALL CLASSES   
33           TOTAL       CROPS                         ALL CLASSES   
34           TOTAL       CROPS                         ALL CLASSES   
35           TOTAL       CROPS                         ALL CLASSES   
36  AREA HARVESTED       CROPS                         ALL CLASSES   
37  AREA HARVESTED       CROPS                         ALL CLASSES   
38  AREA HARVESTED       CROPS                         ALL CLASSES   
39  AREA HARVESTED       CROPS                         ALL CLASSES   
40           TOTAL       CROPS                         ALL CLASSES   
41           TOTAL       CROPS                         ALL CLASSES   
42           TOTAL       CROPS                         ALL CLASSES   
43           TOTAL       CROPS                         ALL CLASSES   
44           TOTAL       CROPS                      (EXCL ALFALFA)   
45           TOTAL       CROPS                             ALFALFA   
46           TOTAL       CROPS                             ALFALFA   
47           TOTAL       CROPS                         SMALL GRAIN   
48           TOTAL       CROPS                         SMALL GRAIN   
49           TOTAL       CROPS                         SMALL GRAIN   
50           TOTAL       CROPS  TAME, (EXCL ALFALFA & SMALL GRAIN)   
51           TOTAL       CROPS  TAME, (EXCL ALFALFA & SMALL GRAIN)   
52           TOTAL       CROPS  TAME, (EXCL ALFALFA & SMALL GRAIN)   
53           TOTAL       CROPS  TAME, (EXCL ALFALFA & SMALL GRAIN)   
54           TOTAL       CROPS                                WILD   
55           TOTAL       CROPS                         ALL CLASSES   
56           TOTA

In [4]:
interesting_column_str = 'GROUP_DESC, COMMODITY_DESC, CLASS_DESC, PRODN_PRACTICE_DESC, \
    UTIL_PRACTICE_DESC, STATISTICCAT_DESC, UNIT_DESC, SHORT_DESC, LOCATION_DESC, DOMAIN_DESC, VALUE'
interesting_column_list = str.split(interesting_column_str)
interesting_columns_fewer_coulumns_str = 'GROUP_DESC, COMMODITY_DESC, STATISTICCAT_DESC, UNIT_DESC, \
    SHORT_DESC, LOCATION_DESC, DOMAIN_DESC, VALUE'
interesting_columns_fewer_coulumns_list = interesting_columns_fewer_coulumns_str.split()
print(interesting_columns_fewer_coulumns_list)

['GROUP_DESC,', 'COMMODITY_DESC,', 'STATISTICCAT_DESC,', 'UNIT_DESC,', 'SHORT_DESC,', 'LOCATION_DESC,', 'DOMAIN_DESC,', 'VALUE']


In [10]:
df_2002 = spark.read.parquet("census_02.parquet")
# Parquet files can also be used to create a temporary view and then used in SQL statements.
df_2002.createOrReplaceTempView("df_2002")

In [3]:
df_2002.limit(100).toPandas().head(100)

SOURCE_DESC         SECTOR_DESC     GROUP_DESC         COMMODITY_DESC  \
0       CENSUS               CROPS     VEGETABLES                  BEANS   
1       CENSUS               CROPS    FIELD CROPS                 COTTON   
2       CENSUS               CROPS    FIELD CROPS                 COTTON   
3       CENSUS               CROPS    FIELD CROPS                 COTTON   
4       CENSUS               CROPS    FIELD CROPS          HAY & HAYLAGE   
5       CENSUS               CROPS    FIELD CROPS                    HAY   
6       CENSUS               CROPS    FIELD CROPS                    HAY   
7       CENSUS               CROPS    FIELD CROPS                    HAY   
8       CENSUS               CROPS    FIELD CROPS                    HAY   
9       CENSUS               CROPS    FIELD CROPS                    HAY   
10      CENSUS               CROPS    FIELD CROPS                    HAY   
11      CENSUS               CROPS    FIELD CROPS                    HAY   
12      CENSUS               CROPS    FIELD CROPS                    HAY   
13      CENSUS               CROPS    FIELD CROPS                    HAY   
14      CENSUS               CROPS    FIELD CROPS                    HAY   
15      CENSUS               CROPS    FIELD CROPS                    RYE   
16      CENSUS               CROPS    FIELD CROPS                    RYE   
17      CENSUS               CROPS    FIELD CROPS               SOYBEANS   
18      CENSUS               CROPS    FIELD CROPS               SOYBEANS   
19      CENSUS               CROPS    FIELD CROPS              SUNFLOWER   
20      CENSUS               CROPS    FIELD CROPS              SUNFLOWER   
21      CENSUS               CROPS    FIELD CROPS              SUNFLOWER   
22      CENSUS               CROPS    FIELD CROPS              SUNFLOWER   
23      CENSUS               CROPS    FIELD CROPS              SUNFLOWER   
24      CENSUS               CROPS    FIELD CROPS              SUNFLOWER   
25      CENSUS               CROPS    FIELD CROPS                  WHEAT   
26      CENSUS               CROPS    FIELD CROPS                  WHEAT   
27      CENSUS               CROPS    FIELD CROPS                  WHEAT   
28      CENSUS               CROPS    FIELD CROPS                  WHEAT   
29      CENSUS               CROPS     VEGETABLES             SWEET CORN   
30      CENSUS               CROPS     VEGETABLES                   OKRA   
31      CENSUS               CROPS     VEGETABLES               PUMPKINS   
32      CENSUS  ANIMALS & PRODUCTS      LIVESTOCK                 CATTLE   
33      CENSUS  ANIMALS & PRODUCTS      LIVESTOCK                   HOGS   
34      CENSUS  ANIMALS & PRODUCTS      LIVESTOCK                  SHEEP   
35      CENSUS           ECONOMICS       EXPENSES                  LABOR   
36      CENSUS           ECONOMICS       EXPENSES                  LABOR   
37      CENSUS           ECONOMICS       EXPENSES                  LABOR   
38      CENSUS           ECONOMICS       EXPENSES          ANIMAL TOTALS   
39      CENSUS           ECONOMICS       EXPENSES                   FEED   
40      CENSUS           ECONOMICS       EXPENSES        CHEMICAL TOTALS   
41      CENSUS           ECONOMICS       EXPENSES               INTEREST   
42      CENSUS           ECONOMICS       EXPENSES  SEEDS & PLANTS TOTALS   
43      CENSUS               CROPS    FIELD CROPS                HAYLAGE   
44      CENSUS               CROPS    FIELD CROPS                HAYLAGE   
45      CENSUS  ANIMALS & PRODUCTS      LIVESTOCK                 CATTLE   
46      CENSUS  ANIMALS & PRODUCTS        POULTRY               CHICKENS   
47      CENSUS  ANIMALS & PRODUCTS      LIVESTOCK                   WOOL   
48      CENSUS  ANIMALS & PRODUCTS      SPECIALTY                  HONEY   
49      CENSUS               CROPS    FIELD CROPS                HAYLAGE   
50      CENSUS               CROPS    FIELD CROPS                HAYLAGE   
51      CENSUS  ANIMALS & PRODUCTS  ANIMAL TOTALS  

In [13]:
only_crops_2002_df = spark.sql("SELECT {} FROM df_2002 WHERE SECTOR_DESC='CROPS'".format(interesting_column_str))
only_crops_2002_df.createOrReplaceTempView("only_crops_2002_df")

In [12]:
check_almonds_COMMOD_DESC_2002_df = spark.sql("\
    SELECT {} FROM only_crops_2002_df WHERE COMMODITY_DESC LIKE 'ALMONDS' \
".format(interesting_columns_fewer_coulumns_str))
check_almonds_COMMOD_DESC_2002_df.createOrReplaceTempView("check_almonds_COMMOD_DESC_2002_df")
check_almonds_COMMOD_DESC_2002_df.toPandas().head(10000)

GROUP_DESC COMMODITY_DESC           STATISTICCAT_DESC   UNIT_DESC  \
0    FRUIT & TREE NUTS        ALMONDS                AREA BEARING       ACRES   
1    FRUIT & TREE NUTS        ALMONDS                AREA BEARING  OPERATIONS   
2    FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING       ACRES   
3    FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING  OPERATIONS   
4    FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING       ACRES   
5    FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING  OPERATIONS   
6    FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING       ACRES   
7    FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING  OPERATIONS   
8    FRUIT & TREE NUTS        ALMONDS                AREA BEARING       ACRES   
9    FRUIT & TREE NUTS        ALMONDS                AREA BEARING  OPERATIONS   
10   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING       ACRES   
11   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING  OPERATIONS   
12   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING       ACRES   
13   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING  OPERATIONS   
14   FRUIT & TREE NUTS        ALMONDS                AREA BEARING       ACRES   
15   FRUIT & TREE NUTS        ALMONDS                AREA BEARING  OPERATIONS   
16   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING       ACRES   
17   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING  OPERATIONS   
18   FRUIT & TREE NUTS        ALMONDS                AREA BEARING       ACRES   
19   FRUIT & TREE NUTS        ALMONDS                AREA BEARING  OPERATIONS   
20   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING       ACRES   
21   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING  OPERATIONS   
22   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING       ACRES   
23   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING  OPERATIONS   
24   FRUIT & TREE NUTS        ALMONDS                AREA BEARING       ACRES   
25   FRUIT & TREE NUTS        ALMONDS                AREA BEARING  OPERATIONS   
26   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING       ACRES   
27   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING  OPERATIONS   
28   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING       ACRES   
29   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING  OPERATIONS   
30   FRUIT & TREE NUTS        ALMONDS                AREA BEARING       ACRES   
31   FRUIT & TREE NUTS        ALMONDS                AREA BEARING  OPERATIONS   
32   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING       ACRES   
33   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING  OPERATIONS   
34   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING       ACRES   
35   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING  OPERATIONS   
36   FRUIT & TREE NUTS        ALMONDS                AREA BEARING       ACRES   
37   FRUIT & TREE NUTS        ALMONDS                AREA BEARING  OPERATIONS   
38   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING       ACRES   
39   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING  OPERATIONS   
40   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING       ACRES   
41   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING  OPERATIONS   
42   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING       ACRES   
43   FRUIT & TREE NUTS        ALMONDS            AREA NON-BEARING  OPERATIONS   
44   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING       ACRES   
45   FRUIT & TREE NUTS        ALMONDS  AREA BEARING & NON-BEARING  OPERATIONS   
46   FRUIT & TREE NUTS        ALMONDS                AREA BEARING       ACRES   
47   FRUIT & TREE NUTS        ALMONDS                AREA BEARING  OPERATIONS   
48   FRUIT & TREE NUTS        ALMONDS  AREA

In [10]:
check_other_COMMOD_DESC_2002_df = spark.sql("\
    SELECT {} FROM only_crops_2002_df WHERE COMMODITY_DESC LIKE '%OTHER%'\
".format(interesting_column_str))
check_other_COMMOD_DESC_2002_df.createOrReplaceTempView("check_other_COMMOD_DESC_2002_df")
check_other_COMMOD_DESC_2002_df.toPandas().tail(10000)

GROUP_DESC            COMMODITY_DESC       CLASS_DESC  \
9767         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9768         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9769         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9770         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9771         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9772         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9773         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9774         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9775         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9776         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9777         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9778         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9779         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9780         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9781         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9782         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9783         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9784         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9785         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9786         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9787         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9788         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9789         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9790         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9791         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9792         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9793         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9794         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9795         FIELD CROPS        FIELD CROPS, OTHER      ALL CLASSES   
9796         FIELD CROPS        FIELD CROPS, OTHER      ALL CLASSES   
9797         FIELD CROPS        FIELD CROPS, OTHER      ALL CLASSES   
9798         FIELD CROPS        FIELD CROPS, OTHER      ALL CLASSES   
9799         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9800         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9801         FIELD CROPS        FIELD CROPS, OTHER      ALL CLASSES   
9802         FIELD CROPS        FIELD CROPS, OTHER      ALL CLASSES   
9803         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9804         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9805         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9806         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9807         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9808         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9809         FIELD CROPS  GRASSES & LEGUMES, OTHER      ALL CLASSES   
9810         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9811         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9812         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9813         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9814         FIELD CROPS        FIELD CROPS, OTHER      ALL CLASSES   
9815         FIELD CROPS        FIELD CROPS, OTHER      ALL CLASSES   
9816         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9817         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9818         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9819         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9820         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9821         FIELD CROPS        FIELD CROPS, OTHER         INCL HAY   
9822          VEGETABLES         VEGET

In [10]:
check_woody_COMMOD_DESC_2002_df = spark.sql("SELECT {} FROM only_crops_2002_df \
    WHERE COMMODITY_DESC LIKE '%CHRISTMAS TREES%' OR COMMODITY_DESC LIKE '%WOODY%' \
    AND STATISTICCAT_DESC NOT LIKE 'SALES'\
".format(interesting_columns_fewer_coulumns_str))
check_woody_COMMOD_DESC_2002_df.createOrReplaceTempView("check_woody_COMMOD_DESC_2002_df")
check_woody_COMMOD_DESC_2002_df.limit(1000).toPandas().tail(1000)

GROUP_DESC                                COMMODITY_DESC  \
0    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
1    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
2    HORTICULTURE                        SHORT TERM WOODY CROPS   
3    HORTICULTURE                        SHORT TERM WOODY CROPS   
4    HORTICULTURE                        SHORT TERM WOODY CROPS   
5    HORTICULTURE                        SHORT TERM WOODY CROPS   
6    HORTICULTURE                           CUT CHRISTMAS TREES   
7    HORTICULTURE                           CUT CHRISTMAS TREES   
8    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
9    HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
10   HORTICULTURE                           CUT CHRISTMAS TREES   
11   HORTICULTURE                           CUT CHRISTMAS TREES   
12   HORTICULTURE                           CUT CHRISTMAS TREES   
13   HORTICULTURE                           CUT CHRISTMAS TREES   
14   HORTICULTURE                        SHORT TERM WOODY CROPS   
15   HORTICULTURE                        SHORT TERM WOODY CROPS   
16   HORTICULTURE                           CUT CHRISTMAS TREES   
17   HORTICULTURE                           CUT CHRISTMAS TREES   
18   HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
19   HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
20   HORTICULTURE                        SHORT TERM WOODY CROPS   
21   HORTICULTURE                        SHORT TERM WOODY CROPS   
22   HORTICULTURE                        SHORT TERM WOODY CROPS   
23   HORTICULTURE                        SHORT TERM WOODY CROPS   
24   HORTICULTURE                           CUT CHRISTMAS TREES   
25   HORTICULTURE                           CUT CHRISTMAS TREES   
26   HORTICULTURE                        SHORT TERM WOODY CROPS   
27   HORTICULTURE                        SHORT TERM WOODY CROPS   
28   HORTICULTURE                           CUT CHRISTMAS TREES   
29   HORTICULTURE                           CUT CHRISTMAS TREES   
30   HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
31   HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
32   HORTICULTURE                        SHORT TERM WOODY CROPS   
33   HORTICULTURE                        SHORT TERM WOODY CROPS   
34   HORTICULTURE                           CUT CHRISTMAS TREES   
35   HORTICULTURE                           CUT CHRISTMAS TREES   
36   HORTICULTURE                           CUT CHRISTMAS TREES   
37   HORTICULTURE                           CUT CHRISTMAS TREES   
38   HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
39   HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
40   HORTICULTURE                        SHORT TERM WOODY CROPS   
41   HORTICULTURE                        SHORT TERM WOODY CROPS   
42   HORTICULTURE                        SHORT TERM WOODY CROPS   
43   HORTICULTURE                        SHORT TERM WOODY CROPS   
44   HORTICULTURE                           CUT CHRISTMAS TREES   
45   HORTICULTURE                           CUT CHRISTMAS TREES   
46   HORTICULTURE                           CUT CHRISTMAS TREES   
47   HORTICULTURE                           CUT CHRISTMAS TREES   
48   HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
49   HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS   
50   HORTICULTURE                           CUT CHRISTMAS TREES   
51   HORTICULTURE                           CUT CHRISTMAS TREES   
52   HORTICULTURE                           CUT CHRISTMAS TREES   
53   HORTICULTURE                           CUT CHRISTMAS TREES   
54   HORTICULTURE                        SHORT TERM WOODY CROPS   
55   HORTICULTURE                        SHORT TERM WOODY CROPS   
56   HORTICULTURE                           CUT CHRISTMAS TREES   
57   HORTICULTURE                           CUT CHRISTMAS TREES   
58   HORTICULTURE  CUT CHRISTMAS TREES & SHORT TERM WO

In [14]:
check_hay_COMMOD_DESC_2002_df = spark.sql("SELECT * FROM only_crops_2002_df WHERE COMMODITY_DESC LIKE '%HAY%'")
check_hay_COMMOD_DESC_2002_df.createOrReplaceTempView("check_hay_COMMOD_DESC_2002_df")
check_hay_COMMOD_DESC_2002_df.limit(100).toPandas().head(100)

GROUP_DESC COMMODITY_DESC                          CLASS_DESC  \
0   FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
1   FIELD CROPS            HAY                         ALL CLASSES   
2   FIELD CROPS            HAY                         ALL CLASSES   
3   FIELD CROPS            HAY                         ALL CLASSES   
4   FIELD CROPS            HAY                             ALFALFA   
5   FIELD CROPS            HAY                             ALFALFA   
6   FIELD CROPS            HAY                             ALFALFA   
7   FIELD CROPS            HAY                         SMALL GRAIN   
8   FIELD CROPS            HAY                         SMALL GRAIN   
9   FIELD CROPS            HAY                                WILD   
10  FIELD CROPS            HAY                                WILD   
11  FIELD CROPS        HAYLAGE                      (EXCL ALFALFA)   
12  FIELD CROPS        HAYLAGE                         ALL CLASSES   
13  FIELD CROPS        HAYLAGE                      (EXCL ALFALFA)   
14  FIELD CROPS        HAYLAGE                         ALL CLASSES   
15  FIELD CROPS            HAY                         ALL CLASSES   
16  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
17  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
18  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
19  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
20  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
21  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
22  FIELD CROPS        HAYLAGE                         ALL CLASSES   
23  FIELD CROPS            HAY                         ALL CLASSES   
24  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
25  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
26  FIELD CROPS        HAYLAGE                      (EXCL ALFALFA)   
27  FIELD CROPS            HAY                             ALFALFA   
28  FIELD CROPS            HAY                             ALFALFA   
29  FIELD CROPS            HAY                         SMALL GRAIN   
30  FIELD CROPS            HAY                         SMALL GRAIN   
31  FIELD CROPS            HAY                         SMALL GRAIN   
32  FIELD CROPS            HAY  TAME, (EXCL ALFALFA & SMALL GRAIN)   
33  FIELD CROPS            HAY  TAME, (EXCL ALFALFA & SMALL GRAIN)   
34  FIELD CROPS            HAY  TAME, (EXCL ALFALFA & SMALL GRAIN)   
35  FIELD CROPS            HAY  TAME, (EXCL ALFALFA & SMALL GRAIN)   
36  FIELD CROPS            HAY  TAME, (EXCL ALFALFA & SMALL GRAIN)   
37  FIELD CROPS            HAY                                WILD   
38  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
39  FIELD CROPS            HAY                         ALL CLASSES   
40  FIELD CROPS            HAY                         ALL CLASSES   
41  FIELD CROPS            HAY                         ALL CLASSES   
42  FIELD CROPS            HAY                             ALFALFA   
43  FIELD CROPS            HAY                             ALFALFA   
44  FIELD CROPS            HAY                         SMALL GRAIN   
45  FIELD CROPS            HAY                         SMALL GRAIN   
46  FIELD CROPS            HAY                                WILD   
47  FIELD CROPS            HAY                                WILD   
48  FIELD CROPS        HAYLAGE                      (EXCL ALFALFA)   
49  FIELD CROPS        HAYLAGE                         ALL CLASSES   
50  FIELD CROPS        HAYLAGE                      (EXCL ALFALFA)   
51  FIELD CROPS        HAYLAGE                         ALL CLASSES   
52  FIELD CROPS            HAY                         ALL CLASSES   
53  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
54  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
55  FIELD CROPS  HAY & HAYLAGE                         ALL CLASSES   
56  FIELD CROPS

In [5]:
check_hay_again_COMMOD_DESC_2002_df = spark.sql("\
        SELECT {} FROM df_2002 WHERE COMMODITY_DESC LIKE 'HAY & HAYLAGE' AND (UNIT_DESC LIKE 'OPERATIONS' \
        OR UNIT_DESC LIKE 'SQ FT' OR UNIT_DESC LIKE 'ACRES') AND PRODN_PRACTICE_DESC = 'ALL PRODUCTION PRACTICES' \
".format(interesting_column_str))
check_hay_again_COMMOD_DESC_2002_df.createOrReplaceTempView("check_hay_again_COMMOD_DESC_2002_df")
check_hay_again_COMMOD_DESC_2002_df.limit(6).toPandas().head(10000)

GROUP_DESC COMMODITY_DESC   CLASS_DESC       PRODN_PRACTICE_DESC  \
0  FIELD CROPS  HAY & HAYLAGE  ALL CLASSES  ALL PRODUCTION PRACTICES   
1  FIELD CROPS  HAY & HAYLAGE  ALL CLASSES  ALL PRODUCTION PRACTICES   
2  FIELD CROPS  HAY & HAYLAGE  ALL CLASSES  ALL PRODUCTION PRACTICES   
3  FIELD CROPS  HAY & HAYLAGE  ALL CLASSES  ALL PRODUCTION PRACTICES   
4  FIELD CROPS  HAY & HAYLAGE  ALL CLASSES  ALL PRODUCTION PRACTICES   
5  FIELD CROPS  HAY & HAYLAGE  ALL CLASSES  ALL PRODUCTION PRACTICES   

          UTIL_PRACTICE_DESC STATISTICCAT_DESC   UNIT_DESC  \
0  ALL UTILIZATION PRACTICES    AREA HARVESTED       ACRES   
1  ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   
2  ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   
3  ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   
4  ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   
5  ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   

                                       SHORT_DESC  \
0                 HAY & HAYLAGE - ACRES HARVESTED   
1  HAY & HAYLAGE - OPERATIONS WITH AREA HARVESTED   
2  HAY & HAYLAGE - OPERATIONS WITH AREA HARVESTED   
3  HAY & HAYLAGE - OPERATIONS WITH AREA HARVESTED   
4  HAY & HAYLAGE - OPERATIONS WITH AREA HARVESTED   
5  HAY & HAYLAGE - OPERATIONS WITH AREA HARVESTED   

                       LOCATION_DESC     DOMAIN_DESC   VALUE  
0  ALABAMA, NORTHERN VALLEY, COLBERT           TOTAL  12,055  
1  ALABAMA, NORTHERN VALLEY, COLBERT           TOTAL     287  
2  ALABAMA, NORTHERN VALLEY, COLBERT  AREA HARVESTED     122  
3  ALABAMA, NORTHERN VALLEY, COLBERT  AREA HARVESTED      26  
4  ALABAMA, NORTHERN VALLEY, COLBERT  AREA HARVESTED     137  
5  ALABAMA, NORTHERN VALLEY, COLBERT  AREA HARVESTED       2

In [56]:
check_cotton_COMMOD_DESC_2002_df = spark.sql("SELECT * FROM df_2002 WHERE COMMODITY_DESC LIKE '%COTTON%'")
check_cotton_COMMOD_DESC_2002_df.createOrReplaceTempView("check_cotton_COMMOD_DESC_2002_df")
check_cotton_COMMOD_DESC_2002_df.limit(6).toPandas().head(6)

SOURCE_DESC SECTOR_DESC   GROUP_DESC COMMODITY_DESC   CLASS_DESC  \
0      CENSUS       CROPS  FIELD CROPS         COTTON  ALL CLASSES   
1      CENSUS       CROPS  FIELD CROPS         COTTON       UPLAND   
2      CENSUS       CROPS  FIELD CROPS         COTTON       UPLAND   
3      CENSUS       CROPS  FIELD CROPS         COTTON  ALL CLASSES   
4      CENSUS       CROPS  FIELD CROPS         COTTON  ALL CLASSES   
5      CENSUS       CROPS  FIELD CROPS         COTTON  ALL CLASSES   

        PRODN_PRACTICE_DESC         UTIL_PRACTICE_DESC STATISTICCAT_DESC  \
0  ALL PRODUCTION PRACTICES  ALL UTILIZATION PRACTICES    AREA HARVESTED   
1  ALL PRODUCTION PRACTICES  ALL UTILIZATION PRACTICES    AREA HARVESTED   
2                 IRRIGATED  ALL UTILIZATION PRACTICES    AREA HARVESTED   
3  ALL PRODUCTION PRACTICES  ALL UTILIZATION PRACTICES    AREA HARVESTED   
4  ALL PRODUCTION PRACTICES  ALL UTILIZATION PRACTICES    AREA HARVESTED   
5  ALL PRODUCTION PRACTICES  ALL UTILIZATION PRACTICES    AREA HARVESTED   

    UNIT_DESC                                   SHORT_DESC     DOMAIN_DESC  \
0       ACRES                     COTTON - ACRES HARVESTED           TOTAL   
1       ACRES             COTTON, UPLAND - ACRES HARVESTED           TOTAL   
2       ACRES  COTTON, UPLAND, IRRIGATED - ACRES HARVESTED           TOTAL   
3  OPERATIONS      COTTON - OPERATIONS WITH AREA HARVESTED           TOTAL   
4  OPERATIONS      COTTON - OPERATIONS WITH AREA HARVESTED  AREA HARVESTED   
5  OPERATIONS      COTTON - OPERATIONS WITH AREA HARVESTED  AREA HARVESTED   

                        DOMAINCAT_DESC AGG_LEVEL_DESC  STATE_ANSI  \
0                        NOT SPECIFIED         COUNTY         1.0   
1                        NOT SPECIFIED         COUNTY         1.0   
2                        NOT SPECIFIED         COUNTY         1.0   
3                        NOT SPECIFIED         COUNTY         1.0   
4  AREA HARVESTED: (1.0 TO 24.9 ACRES)         COUNTY         1.0   
5   AREA HARVESTED: (100 TO 249 ACRES)         COUNTY         1.0   

   STATE_FIPS_CODE STATE_ALPHA STATE_NAME  ASD_CODE         ASD_DESC  \
0              1.0          AL    ALABAMA      10.0  NORTHERN VALLEY   
1              1.0          AL    ALABAMA      10.0  NORTHERN VALLEY   
2              1.0          AL    ALABAMA      10.0  NORTHERN VALLEY   
3              1.0          AL    ALABAMA      10.0  NORTHERN VALLEY   
4              1.0          AL    ALABAMA      10.0  NORTHERN VALLEY   
5              1.0          AL    ALABAMA      10.0  NORTHERN VALLEY   

   COUNTY_ANSI  COUNTY_CODE COUNTY_NAME REGION_DESC ZIP_5  WATERSHED_CODE  \
0         33.0         33.0     COLBERT        None  None             0.0   
1         33.0         33.0     COLBERT        None  None             0.0   
2         33.0         33.0     COLBERT        None  None             0.0   
3         33.0         33.0     COLBERT        None  None             0.0   
4         33.0         33.0     COLBERT        None  None             0.0   
5         33.0         33.0     COLBERT        None  None             0.0   

  WATERSHED_DESC CONGR_DISTRICT_CODE  COUNTRY_CODE   COUNTRY_NAME  \
0           None                None        9000.0  UNITED STATES   
1           None                None        9000.0  UNITED STATES   
2           None                None        9000.0  UNITED STATES   
3           None                None        9000.0  UNITED STATES   
4           None                None        9000.0  UNITED STATES   
5           None                None        9000.0  UNITED STATES   

                       LOCATION_DESC    YEAR FREQ_DESC  BEGIN_CODE  END_CODE  \
0  ALABAMA, NORTHERN VALLEY, COLBERT  2002.0    ANNUAL         0.0       0.0   
1  ALABAMA, NORTHERN VALLEY, COLBERT  2002.0    ANNUAL         0.0       0.0   
2  ALABAMA, NORTHERN VALLEY, COLBERT  2002.0    ANNUAL         0.0       0.0   
3  ALABAMA, NORTHERN VALLEY, COLBERT  2002.0    ANNUAL         0.0       0.0   
4  ALABAMA, NORTHE

In [11]:
check_tubers_COMMOD_DESC_2002_df = spark.sql("\
    SELECT {} FROM only_crops_2002_df WHERE COMMODITY_DESC LIKE '%TUBERS%' OR COMMODITY_DESC LIKE 'TARO' \
".format(interesting_columns_fewer_coulumns_str))
check_tubers_COMMOD_DESC_2002_df.createOrReplaceTempView("check_tubers_COMMOD_DESC_2002_df")
check_tubers_COMMOD_DESC_2002_df.toPandas().head(10000)

GROUP_DESC                     COMMODITY_DESC   STATISTICCAT_DESC  \
0     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
1     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
2     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
3     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
4     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
5     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
6     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
7     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
8     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
9     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
10    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
11    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
12    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
13    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
14    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
15    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
16    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
17    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
18    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
19    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
20    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
21    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
22    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
23    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
24    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
25    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
26    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
27    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
28    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
29    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
30    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
31    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
32    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
33    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
34    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
35    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
36    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
37    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
38    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
39    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
40    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
41    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
42    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
43    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
44    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
45    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
46    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
47    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
48    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
49    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
50    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
51  

In [17]:
check_ginger_corms_COMMOD_DESC_2002_df = spark.sql("\
    SELECT {} FROM only_crops_2002_df WHERE COMMODITY_DESC LIKE '%TUBERS%' OR COMMODITY_DESC LIKE 'GINGER ROOT' \
".format(interesting_columns_fewer_coulumns_str))
check_ginger_corms_COMMOD_DESC_2002_df.createOrReplaceTempView("check_ginger_corms_COMMOD_DESC_2002_df")
check_ginger_corms_COMMOD_DESC_2002_df.toPandas().head(10000)

GROUP_DESC                     COMMODITY_DESC   STATISTICCAT_DESC  \
0     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
1     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
2     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
3     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
4     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
5     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
6     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
7     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
8     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
9     HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
10    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
11    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
12    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
13    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
14    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
15    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
16    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
17    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
18    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
19    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
20    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
21    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
22    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
23    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
24    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
25    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
26    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
27    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
28    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
29    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
30    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
31    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
32    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
33    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
34    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
35    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
36    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
37    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
38    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
39    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
40    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
41    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
42    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
43    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
44    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
45    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
46    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
47    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
48    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
49    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
50    HORTICULTURE  BULBS & CORMS & RHIZOMES & TUBERS  AREA IN PRODUCTION   
51  

In [14]:
check_ginger_COMMOD_DESC_2002_df = spark.sql("\
    SELECT {} FROM only_crops_2002_df WHERE COMMODITY_DESC LIKE 'GINGER ROOT' \
".format(interesting_columns_fewer_coulumns_str))
check_ginger_COMMOD_DESC_2002_df.createOrReplaceTempView("check_ginger_COMMOD_DESC_2002_df")
check_ginger_COMMOD_DESC_2002_df.toPandas().head(10000)

GROUP_DESC COMMODITY_DESC STATISTICCAT_DESC   UNIT_DESC  \
0   VEGETABLES    GINGER ROOT    AREA HARVESTED       ACRES   
1   VEGETABLES    GINGER ROOT        PRODUCTION          LB   
2   VEGETABLES    GINGER ROOT    AREA HARVESTED  OPERATIONS   
3   VEGETABLES    GINGER ROOT    AREA HARVESTED       ACRES   
4   VEGETABLES    GINGER ROOT    AREA HARVESTED  OPERATIONS   
5   VEGETABLES    GINGER ROOT    AREA HARVESTED       ACRES   
6   VEGETABLES    GINGER ROOT        PRODUCTION          LB   
7   VEGETABLES    GINGER ROOT    AREA HARVESTED  OPERATIONS   
8   VEGETABLES    GINGER ROOT    AREA HARVESTED       ACRES   
9   VEGETABLES    GINGER ROOT    AREA HARVESTED  OPERATIONS   
10  VEGETABLES    GINGER ROOT    AREA HARVESTED       ACRES   
11  VEGETABLES    GINGER ROOT        PRODUCTION          LB   
12  VEGETABLES    GINGER ROOT    AREA HARVESTED  OPERATIONS   
13  VEGETABLES    GINGER ROOT    AREA HARVESTED       ACRES   
14  VEGETABLES    GINGER ROOT    AREA HARVESTED  OPERATIONS   
15  VEGETABLES    GINGER ROOT    AREA HARVESTED       ACRES   
16  VEGETABLES    GINGER ROOT        PRODUCTION          LB   
17  VEGETABLES    GINGER ROOT    AREA HARVESTED  OPERATIONS   
18  VEGETABLES    GINGER ROOT    AREA HARVESTED       ACRES   
19  VEGETABLES    GINGER ROOT    AREA HARVESTED  OPERATIONS   
20  VEGETABLES    GINGER ROOT    AREA HARVESTED       ACRES   
21  VEGETABLES    GINGER ROOT        PRODUCTION          LB   
22  VEGETABLES    GINGER ROOT    AREA HARVESTED  OPERATIONS   
23  VEGETABLES    GINGER ROOT    AREA HARVESTED       ACRES   
24  VEGETABLES    GINGER ROOT    AREA HARVESTED  OPERATIONS   
25  VEGETABLES    GINGER ROOT    AREA HARVESTED       ACRES   
26  VEGETABLES    GINGER ROOT        PRODUCTION          LB   
27  VEGETABLES    GINGER ROOT    AREA HARVESTED  OPERATIONS   
28  VEGETABLES    GINGER ROOT    AREA HARVESTED       ACRES   
29  VEGETABLES    GINGER ROOT    AREA HARVESTED  OPERATIONS   

                                           SHORT_DESC  \
0                       GINGER ROOT - ACRES HARVESTED   
1            GINGER ROOT - PRODUCTION, MEASURED IN LB   
2        GINGER ROOT - OPERATIONS WITH AREA HARVESTED   
3            GINGER ROOT, IRRIGATED - ACRES HARVESTED   
4   GINGER ROOT, IRRIGATED - OPERATIONS WITH AREA ...   
5                       GINGER ROOT - ACRES HARVESTED   
6            GINGER ROOT - PRODUCTION, MEASURED IN LB   
7        GINGER ROOT - OPERATIONS WITH AREA HARVESTED   
8            GINGER ROOT, IRRIGATED - ACRES HARVESTED   
9   GINGER ROOT, IRRIGATED - OPERATIONS WITH AREA ...   
10                      GINGER ROOT - ACRES HARVESTED   
11           GINGER ROOT - PRODUCTION, MEASURED IN LB   
12       GINGER ROOT - OPERATIONS WITH AREA HARVESTED   
13           GINGER ROOT, IRRIGATED - ACRES HARVESTED   
14  GINGER ROOT, IRRIGATED - OPERATIONS WITH AREA ...   
15                      GINGER ROOT - ACRES HARVESTED   
16           GINGER ROOT - PRODUCTION, MEASURED IN LB   
17       GINGER ROOT - OPERATIONS WITH AREA HARVESTED   
18           GINGER ROOT, IRRIGATED - ACRES HARVESTED   
19  GINGER ROOT, IRRIGATED - OPERATIONS WITH AREA ...   
20                      GINGER ROOT - ACRES HARVESTED   
21           GINGER ROOT - PRODUCTION, MEASURED IN LB   
22       GINGER ROOT - OPERATIONS WITH AREA HARVESTED   
23           GINGER ROOT, IRRIGATED - ACRES HARVESTED   
24  GINGER ROOT, IRRIGATED - OPERATIONS WITH AREA ...   
25                      GINGER ROOT - ACRES HARVESTED   
26           GINGER ROOT - PRODUCTION, MEASURED IN LB   
27       GINGER ROOT - OPERATIONS WITH AREA HARVESTED   
28           GINGER ROOT, IRRIGATED - ACRES HARVESTED   
29  GINGER ROOT, IRRIGATED - OPERATIONS WITH AREA ...   

                                        LOCATION_DESC DOMAIN_DESC      VALUE  
0                       HAWAII, HAWAII ISLAND, HAWAII       TOTAL        165  
1                       HAWAII, HAWAII ISLAND, HAWAII       TOTAL  4,848,145  
2                       HAWAII, HAWAII ISLAND

In [10]:
check_ginger2_COMMOD_DESC_2002_df = spark.sql("\
    SELECT {} DOMAIN_DESC FROM only_crops_2002_df WHERE COMMODITY_DESC LIKE 'GINGER ROOT' \
".format(interesting_column_str))
check_ginger2_COMMOD_DESC_2002_df.createOrReplaceTempView("check_ginger2_COMMOD_DESC_2002_df")
check_ginger2_COMMOD_DESC_2002_df.toPandas().head(10000)

GROUP_DESC COMMODITY_DESC   CLASS_DESC       PRODN_PRACTICE_DESC  \
0   VEGETABLES    GINGER ROOT  ALL CLASSES  ALL PRODUCTION PRACTICES   
1   VEGETABLES    GINGER ROOT  ALL CLASSES  ALL PRODUCTION PRACTICES   
2   VEGETABLES    GINGER ROOT  ALL CLASSES  ALL PRODUCTION PRACTICES   
3   VEGETABLES    GINGER ROOT  ALL CLASSES                 IRRIGATED   
4   VEGETABLES    GINGER ROOT  ALL CLASSES                 IRRIGATED   
5   VEGETABLES    GINGER ROOT  ALL CLASSES  ALL PRODUCTION PRACTICES   
6   VEGETABLES    GINGER ROOT  ALL CLASSES  ALL PRODUCTION PRACTICES   
7   VEGETABLES    GINGER ROOT  ALL CLASSES  ALL PRODUCTION PRACTICES   
8   VEGETABLES    GINGER ROOT  ALL CLASSES                 IRRIGATED   
9   VEGETABLES    GINGER ROOT  ALL CLASSES                 IRRIGATED   
10  VEGETABLES    GINGER ROOT  ALL CLASSES  ALL PRODUCTION PRACTICES   
11  VEGETABLES    GINGER ROOT  ALL CLASSES  ALL PRODUCTION PRACTICES   
12  VEGETABLES    GINGER ROOT  ALL CLASSES  ALL PRODUCTION PRACTICES   
13  VEGETABLES    GINGER ROOT  ALL CLASSES                 IRRIGATED   
14  VEGETABLES    GINGER ROOT  ALL CLASSES                 IRRIGATED   
15  VEGETABLES    GINGER ROOT  ALL CLASSES  ALL PRODUCTION PRACTICES   
16  VEGETABLES    GINGER ROOT  ALL CLASSES  ALL PRODUCTION PRACTICES   
17  VEGETABLES    GINGER ROOT  ALL CLASSES  ALL PRODUCTION PRACTICES   
18  VEGETABLES    GINGER ROOT  ALL CLASSES                 IRRIGATED   
19  VEGETABLES    GINGER ROOT  ALL CLASSES                 IRRIGATED   
20  VEGETABLES    GINGER ROOT  ALL CLASSES  ALL PRODUCTION PRACTICES   
21  VEGETABLES    GINGER ROOT  ALL CLASSES  ALL PRODUCTION PRACTICES   
22  VEGETABLES    GINGER ROOT  ALL CLASSES  ALL PRODUCTION PRACTICES   
23  VEGETABLES    GINGER ROOT  ALL CLASSES                 IRRIGATED   
24  VEGETABLES    GINGER ROOT  ALL CLASSES                 IRRIGATED   
25  VEGETABLES    GINGER ROOT  ALL CLASSES  ALL PRODUCTION PRACTICES   
26  VEGETABLES    GINGER ROOT  ALL CLASSES  ALL PRODUCTION PRACTICES   
27  VEGETABLES    GINGER ROOT  ALL CLASSES  ALL PRODUCTION PRACTICES   
28  VEGETABLES    GINGER ROOT  ALL CLASSES                 IRRIGATED   
29  VEGETABLES    GINGER ROOT  ALL CLASSES                 IRRIGATED   

           UTIL_PRACTICE_DESC STATISTICCAT_DESC   UNIT_DESC  \
0   ALL UTILIZATION PRACTICES    AREA HARVESTED       ACRES   
1   ALL UTILIZATION PRACTICES        PRODUCTION          LB   
2   ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   
3   ALL UTILIZATION PRACTICES    AREA HARVESTED       ACRES   
4   ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   
5   ALL UTILIZATION PRACTICES    AREA HARVESTED       ACRES   
6   ALL UTILIZATION PRACTICES        PRODUCTION          LB   
7   ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   
8   ALL UTILIZATION PRACTICES    AREA HARVESTED       ACRES   
9   ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   
10  ALL UTILIZATION PRACTICES    AREA HARVESTED       ACRES   
11  ALL UTILIZATION PRACTICES        PRODUCTION          LB   
12  ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   
13  ALL UTILIZATION PRACTICES    AREA HARVESTED       ACRES   
14  ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   
15  ALL UTILIZATION PRACTICES    AREA HARVESTED       ACRES   
16  ALL UTILIZATION PRACTICES        PRODUCTION          LB   
17  ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   
18  ALL UTILIZATION PRACTICES    AREA HARVESTED       ACRES   
19  ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   
20  ALL UTILIZATION PRACTICES    AREA HARVESTED       ACRES   
21  ALL UTILIZATION PRACTICES        PRODUCTION          LB   
22  ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   
23  ALL UTILIZATION PRACTICES    AREA HARVESTED       ACRES   
24  ALL UTILIZATION PRACTICES    AREA HARVESTED  OPERATIONS   
25  ALL UTILIZATION PRACTICES    AREA HARVESTED       ACRES   
26  ALL UTILIZATION PRACTICES        PRODUCTION          LB   
27  ALL

In [ ]:
to_check_list =  ['FIELD CROPS, OTHER','GRASSES & LEGUMES, OTHER', 'FRUIT & TREE NUTS, OTHER', 'SHORT TERM WOODY CROPS', 'CUT CHRISTMAS TREES & SHORT TERM WOODY CROPS', ]

In [8]:
distinct_production_df = spark.sql('SELECT DISTINCT PRODN_PRACTICE_DESC from only_crops_2002_df')
distinct_production_df.show(250, False)

+-------------------------------------------------------+
|PRODN_PRACTICE_DESC                                    |
+-------------------------------------------------------+
|IRRIGATED, ENTIRE CROP                                 |
|IRRIGATED                                              |
|IN THE OPEN, IRRIGATED, PART OF CROP, IRRIGATED PORTION|
|UNDER PROTECTION                                       |
|IN THE OPEN                                            |
|IRRIGATED, PART OF CROP, IRRIGATED PORTION             |
|IRRIGATED, PART OF CROP                                |
|IN THE OPEN, IRRIGATED                                 |
|IN THE OPEN, IRRIGATED, PART OF CROP                   |
|PRODUCTION CONTRACT                                    |
|ALL PRODUCTION PRACTICES                               |
|IRRIGATED, NONE OF CROP                                |
|IN THE OPEN, IRRIGATED, NONE OF CROP                   |
|IN THE OPEN, IRRIGATED, ENTIRE CROP                    |
+-------------

In [7]:
distinct_statisticcat_df = spark.sql('select distinct STATISTICCAT_DESC from only_crops_2002_df')
distinct_statisticcat_df.show(250, False)

+--------------------------+
|STATISTICCAT_DESC         |
+--------------------------+
|PRODUCTION                |
|TAPS                      |
|AREA BEARING              |
|SALES                     |
|AREA NON-BEARING          |
|AREA IN PRODUCTION        |
|AREA GROWN                |
|CAPACITY                  |
|YIELD                     |
|AREA HARVESTED            |
|AREA BEARING & NON-BEARING|
|AREA NOT HARVESTED        |
+--------------------------+



In [15]:
distinct_commodity_df = spark.sql("SELECT DISTINCT COMMODITY_DESC FROM only_crops_2002_df")
#distinct_commodity_df.take(50)
distinct_commodity_df.show(250, False)                                 

+--------------------------------------------+
|COMMODITY_DESC                              |
+--------------------------------------------+
|TANGELOS                                    |
|OATS                                        |
|TEMPLES                                     |
|PEAS                                        |
|PASSION FRUIT                               |
|CRAMBE                                      |
|SORGHUM                                     |
|RYE                                         |
|AMARANTH                                    |
|FIELD CROPS, OTHER                          |
|TARO                                        |
|TANGERINES                                  |
|ARTICHOKES                                  |
|PAPAYAS                                     |
|CUCUMBERS                                   |
|BOYSENBERRIES                               |
|POMEGRANATES                                |
|PEACHES                                     |
|CARROTS     

In [9]:
distinct_units_df = spark.sql('select distinct UNIT_DESC from only_crops_2002_df')
distinct_units_df.show(250, False)

+-----------------+
|UNIT_DESC        |
+-----------------+
|CWT              |
|TONS / ACRE      |
|PCT OF FARM SALES|
|CWT / ACRE       |
|BU               |
|GALLONS          |
|OPERATIONS       |
|LB               |
|BU / OPERATION   |
|TREES            |
|TONS             |
|BALES / ACRE     |
|SQ FT            |
|LB / ACRE        |
|TONS, DRY BASIS  |
|BALES            |
|BU / ACRE        |
|ACRES            |
|NUMBER           |
|$                |
+-----------------+

